**NF Corpus** - complete execution

*   List item
*   List item



In [ ]:
!apt-get install openjdk-21-jdk-headless -y
import os
os.environ["JAVA_HOME"] = "/usr/lib/jvm/java-21-openjdk-amd64/"

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
openjdk-21-jdk-headless is already the newest version (21.0.5+11-1ubuntu1~22.04).
0 upgraded, 0 newly installed, 0 to remove and 49 not upgraded.


In [ ]:

!pip3 install rank_bm25
!pip3 install pyserini

In [ ]:
!pip install pyserini --upgrade

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
import os
import numpy as np
from typing import List, Dict, Tuple
from dataclasses import dataclass
import torch
from transformers import AutoModel, AutoTokenizer
from rank_bm25 import BM25Okapi
# from pyserini.search.lucene import LuceneSearcher
# from pyserini.index import IndexReader
# import openai

In [ ]:
@dataclass
class QOQAConfig:
    """Configuration for QOQA system"""
    # max_iterations: int = 50
    max_iterations: int = 3

    num_initial_docs: int = 5
    num_top_queries: int = 3
    initial_rephrased: int = 3
    iterations_rephrased: int = 1
    temperature: float = 1.0
    bm25_k1: float = 1.2
    bm25_b: float = 0.75
    hybrid_alpha: float = 0.1


In [ ]:
class DenseRetriever:
    """Dense retrieval using BGE embeddings"""
    def __init__(self, model_name: str = "BAAI/bge-base-en-v1.5"):
        self.device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
        self.tokenizer = AutoTokenizer.from_pretrained(model_name)
        self.model = AutoModel.from_pretrained(model_name).to(self.device)

    def encode(self, texts: List[str], batch_size: int = 32) -> np.ndarray:
        print("encode - start- Dense Retriever done")
        embeddings = []
        for i in range(0, len(texts), batch_size):
            batch = texts[i:i + batch_size]
            batch = [f"Represent this sentence for searching relevant passages: {text}"
                     for text in batch]
            inputs = self.tokenizer(batch, padding=True, truncation=True,
                                    return_tensors="pt").to(self.device)
            with torch.no_grad():
                outputs = self.model(**inputs)
                batch_embeddings = outputs.last_hidden_state[:, 0].cpu().numpy()
                embeddings.append(batch_embeddings)
        ans = np.vstack(embeddings)
        print("encode - end -Dense Retriever done")
        # print(ans)
        return ans

In [ ]:
class SparseRetriever:
    """BM25-based sparse retrieval"""
    def __init__(self, documents: List[str]):
        self.tokenized_docs = [doc.split() for doc in documents]
        self.bm25 = BM25Okapi(self.tokenized_docs)

    def get_scores(self, query: str) -> np.ndarray:
        print("get_scores - start- SparseRetriever")
        tokenized_query = query.split()
        res = np.array(self.bm25.get_scores(tokenized_query))

        print("get_scores - end- SparseRetriever")
        print(res)
        return res



In [ ]:
# from openai import OpenAI

class QOQA:
    def __init__(self, config: QOQAConfig, documents: List[str], openai_api_key: str):
        self.config = config
        self.documents = documents
        self.dense_retriever = DenseRetriever()
        self.sparse_retriever = SparseRetriever(documents)
        self.doc_embeddings = self.dense_retriever.encode(documents)
        # openai.api_key = openai_api_key
        self.openai_api_key=openai_api_key

    def get_hybrid_scores(self, query: str) -> np.ndarray:
        print("get__hybrid_scores - start- QOQA")
        bm25_scores = self.sparse_retriever.get_scores(query)
        # hybrid_scores = bm25_scores
        query_embedding = self.dense_retriever.encode([query])[0]
        dense_scores = np.dot(self.doc_embeddings, query_embedding)
        hybrid_scores = (self.config.hybrid_alpha * bm25_scores +
                         (1 - self.config.hybrid_alpha) * dense_scores)
        print(hybrid_scores)
        print("get__hybrid_scores - end- QOQA")
        return hybrid_scores

    def generate_rephrased_query(self, original_query: str, top_docs: List[str], query_bucket: List[Tuple[str, float]]) -> str:
        print("generate_rephrased_query - start- QOQA")
        prompt = self._create_prompt(original_query, top_docs, query_bucket)
        # client = OpenAI(api_key=self.openai_api_key)
        client = OpenAI(api_key="<enter your openai key here>")
        response = client.chat.completions.create(
            model="gpt-3.5-turbo",
            messages=[{"role": "user", "content": prompt}],
            temperature=self.config.temperature
        )

        rephrased_query = response.choices[0].message.content.strip("[]")
        print("generate_rephrased_query - end- QOQA")
        print(rephrased_query)
        return rephrased_query

    def _create_prompt(self, original_query: str, top_docs: List[str], query_bucket: List[Tuple[str, float]]) -> str:
        print("_create_prompt - start- QOQA")
        prompt = f"My goal is to make a rephrased query to retrieve answer documents with high scores.\n"
        prompt += f"Query: {original_query}\n\n"
        prompt += f"Top-{len(top_docs)} retrieved docs:\n"
        for idx, doc in enumerate(top_docs, 1):
            prompt += f"{idx}. {doc[:200]}...\n"
        prompt += "\nExamples of rephrased queries and scores:\n"
        for query, score in query_bucket:
            prompt += f"Rephrased query: {query}\nScore: {score:.2f}\n\n"
        prompt += "Write a new rephrased query in square brackets."
        print("_create_prompt - end - QOQA")
        print(prompt)
        return prompt

    def optimize_query(self, query: str) -> str:
        print("optimize_query - start- QOQA")
        query_bucket = []
        best_query = query
        best_score = float('-inf')
        scores = self.get_hybrid_scores(query)
        top_indices = np.argsort(scores)[-self.config.num_initial_docs:]
        top_docs = [self.documents[i] for i in top_indices]
        for _ in range(self.config.initial_rephrased):
            rephrased = self.generate_rephrased_query(query, top_docs, query_bucket)
            score = np.mean(self.get_hybrid_scores(rephrased))
            query_bucket.append((rephrased, score))
            if score > best_score:
                best_score = score
                best_query = rephrased
        for _ in range(self.config.max_iterations):
            query_bucket.sort(key=lambda x: x[1])
            query_bucket = query_bucket[-self.config.num_top_queries:]
            rephrased = self.generate_rephrased_query(query, top_docs, query_bucket)
            score = np.mean(self.get_hybrid_scores(rephrased))
            query_bucket.append((rephrased, score))
            if score > best_score:
                best_score = score
                best_query = rephrased
            if len(query_bucket) > 5 and all(abs(x[1] - score) < 1e-4 for x in query_bucket[-5:]):
                break
        print("optimize_query - end- QOQA")
        print(best_query)
        return best_query



In [ ]:
!pip install datasets

In [ ]:
from datasets import load_dataset

In [ ]:
# Load the BEIR MSMARCO dataset
dataset = load_dataset("beir/nfcorpus", "corpus")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


In [ ]:
dataset

DatasetDict({
    corpus: Dataset({
        features: ['_id', 'title', 'text'],
        num_rows: 3633
    })
})

In [ ]:
dataset_q = load_dataset("beir/nfcorpus", "queries")

In [ ]:
dataset_q

DatasetDict({
    queries: Dataset({
        features: ['_id', 'title', 'text'],
        num_rows: 3237
    })
})

In [ ]:
dataset_qrel = load_dataset("BeIR/nfcorpus-qrels", split="validation")

In [ ]:
dataset_qrel

Dataset({
    features: ['query-id', 'corpus-id', 'score'],
    num_rows: 11385
})

In [ ]:
from collections import defaultdict

# Initialize a defaultdict to store query-doc pairs
qrels = defaultdict(dict)

# Iterate over the dataset and populate the dictionary
for qrel in dataset_qrel:
    qrels[qrel["query-id"]][qrel["corpus-id"]] = qrel["score"]

# Convert defaultdict back to a regular dictionary if needed
qrels = dict(qrels)

In [ ]:
queries = {query["_id"]: query["text"] for query in dataset_q["queries"]}

In [ ]:
corpus = {doc["_id"]: doc['text'] for doc in dataset["corpus"]}

In [ ]:
print(f"Corpus size: {len(corpus)}")
print(f"Number of queries: {len(queries)}")
print(f"Number of query-document pairs: {len(qrels)}")

Corpus size: 3633
Number of queries: 3237
Number of query-document pairs: 324


In [ ]:
len(corpus)

3633

In [ ]:
documents = list(corpus.values())


In [ ]:
doc_ids = list(corpus.keys())

In [ ]:
len(documents)

3633

In [ ]:
documents[2]

"The aims of this study were to determine the concentrations of 4-nonylphenol (NP) and 4-octylphenol (OP) in 59 human milk samples and to examine related factors including mothers' demographics and dietary habits. Women who consumed over the median amount of cooking oil had significantly higher OP concentrations (0.98 ng/g) than those who consumed less (0.39 ng/g) (P < 0.05). OP concentration was significantly associated with the consumption of cooking oil (beta = 0.62, P < 0.01) and fish oil capsules (beta = 0.39, P < 0.01) after adjustment for age and body mass index (BMI). NP concentration was also significantly associated with the consumption of fish oil capsules (beta = 0.38, P < 0.01) and processed fish products (beta = 0.59, P < 0.01). The food pattern of cooking oil and processed meat products from factor analysis was strongly associated with OP concentration in human milk (P < 0.05). These determinations should aid in suggesting foods for consumption by nursing mothers in orde

In [ ]:
openai_api_key = "<enter your openaikey>"

In [ ]:
config = QOQAConfig()

In [ ]:
qoqa = QOQA(config, documents, openai_api_key=openai_api_key)

encode - start- Dense Retriever done
encode - end -Dense Retriever done


In [ ]:
 # Optimize a sample query
original_query = "CCL19 is absent within dLNs"
optimized_query = qoqa.optimize_query(original_query)

print(f"Original query: {original_query}")
print(f"Optimized query: {optimized_query}")

optimize_query - start- QOQA
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[0.         0.         0.         ... 0.         6.18298326 1.68171687]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[103.30092621 103.36120605 102.74776459 ...  90.81803894  86.08463744
 101.81782226]
get__hybrid_scores - end- QOQA
generate_rephrased_query - start- QOQA
_create_prompt - start- QOQA
_create_prompt - end - QOQA
My goal is to make a rephrased query to retrieve answer documents with high scores.
Query: CCL19 is absent within dLNs

Top-5 retrieved docs:
1. Naturally developing xenospecific Abs are well-documented barriers to xenograft transplantation in humans, but whether analogous xenoreactive T cell immunity develops is not known. We used an enzyme-l...
2. In a prelminary communication, we described the establishment of a continuous human myeloid cell line (HL-60). Here we report the detailed properties of this ce

In [ ]:
# pip install --upgrade openai


In [ ]:
!pip3 install openai==1.55.3 httpx==0.27.2


In [ ]:
!pip3 show openai


In [ ]:
print(queries)

{'PLAIN-3': 'Breast Cancer Cells Feed on Cholesterol', 'PLAIN-4': 'Using Diet to Treat Asthma and Eczema', 'PLAIN-5': 'Treating Asthma With Plants vs. Pills', 'PLAIN-6': 'How Fruits and Vegetables Can Treat Asthma', 'PLAIN-7': 'How Fruits and Vegetables Can Prevent Asthma', 'PLAIN-8': 'Our Tax Dollars Subsidize Unhealthy Foods', 'PLAIN-9': 'Reducing Arsenic in Chicken and Rice', 'PLAIN-10': 'How Contaminated Are Our Children?', 'PLAIN-14': 'Blood Type Diet Perceived as "Crass Fraud"', 'PLAIN-15': 'Why Do Heart Doctors Favor Surgery and Drugs Over Diet?', 'PLAIN-16': 'Phytates in Beans: Anti-Nutrient or Anti-Cancer?', 'PLAIN-17': 'How Phytates Fight Cancer Cells', 'PLAIN-18': 'Colon Cancer Prevention: Is it the Fiber or the Phytates?', 'PLAIN-19': 'Low Carb Diets Found to Feed Heart Disease', 'PLAIN-20': 'How Curry Can Kill Cancer Cells', 'PLAIN-21': 'Testing Turmeric on Smokers', 'PLAIN-24': 'Alkylphenol Endocrine Disruptors and Allergies', 'PLAIN-25': 'Slowing Cognitive Decline with B

In [ ]:
qrels.keys()

dict_keys(['PLAIN-1', 'PLAIN-11', 'PLAIN-22', 'PLAIN-32', 'PLAIN-43', 'PLAIN-55', 'PLAIN-67', 'PLAIN-77', 'PLAIN-90', 'PLAIN-101', 'PLAIN-111', 'PLAIN-122', 'PLAIN-132', 'PLAIN-142', 'PLAIN-152', 'PLAIN-164', 'PLAIN-174', 'PLAIN-185', 'PLAIN-195', 'PLAIN-206', 'PLAIN-216', 'PLAIN-226', 'PLAIN-237', 'PLAIN-247', 'PLAIN-258', 'PLAIN-269', 'PLAIN-279', 'PLAIN-290', 'PLAIN-304', 'PLAIN-319', 'PLAIN-331', 'PLAIN-343', 'PLAIN-357', 'PLAIN-370', 'PLAIN-382', 'PLAIN-394', 'PLAIN-406', 'PLAIN-417', 'PLAIN-428', 'PLAIN-440', 'PLAIN-456', 'PLAIN-467', 'PLAIN-477', 'PLAIN-487', 'PLAIN-498', 'PLAIN-508', 'PLAIN-519', 'PLAIN-530', 'PLAIN-540', 'PLAIN-550', 'PLAIN-560', 'PLAIN-570', 'PLAIN-582', 'PLAIN-592', 'PLAIN-602', 'PLAIN-612', 'PLAIN-622', 'PLAIN-633', 'PLAIN-644', 'PLAIN-656', 'PLAIN-670', 'PLAIN-680', 'PLAIN-690', 'PLAIN-700', 'PLAIN-710', 'PLAIN-720', 'PLAIN-730', 'PLAIN-740', 'PLAIN-750', 'PLAIN-760', 'PLAIN-770', 'PLAIN-781', 'PLAIN-791', 'PLAIN-805', 'PLAIN-816', 'PLAIN-826', 'PLAIN-837'

In [ ]:
from tqdm import tqdm

In [ ]:
# bm25 i=3, qrels=5

In [ ]:
ndcg_scores_optimized = []
ndcg_scores_sparse = []
test_dict={}
test_dict_2={}
query_ids = list(qrels.keys())[:100]
for qid in tqdm(query_ids):
    # Original query retrieval
    # original_hits = model.sparse_retriever.search(queries[qid], k=10)
    # original_docs = [hit.docid for hit in original_hits]
    bm25_scores = qoqa.sparse_retriever.get_scores(queries[qid])
    top_n = 10
    top_n_docids_with_indices = sorted(
        enumerate(bm25_scores),  # Pair (index, score)
        key=lambda x: x[1],  # Sort by score
        reverse=True  # Descending order
    )[:top_n]
    top_n_docids = [doc_ids[idx] for idx, score in top_n_docids_with_indices]  # Extract indices
    top_n_scores = [score for idx, score in top_n_docids_with_indices]
    # top_n_docids = sorted(range(len(bm25_scores)), key=lambda i: bm25_scores[i], reverse=True)[:10]
    test_dict[qid]={}

    for i in range(0,top_n):
      passageid= top_n_docids[i]
      test_dict[qid][passageid]=top_n_scores[i]
    # sorted_passages = sorted(test_dict[qid].items(), key=lambda item: item[1], reverse=True)
    # test_dict[qid] = dict(sorted_passages[:10])


    # print(test_dict)

    # Calculate original NDCG@10
    # original_ndcg = calculate_ndcg(top_n_docids, filtered_qrels[str(qid)], k=10)

    # Optimize query
    optimized_query = qoqa.optimize_query(queries[qid])

    # Optimized query retrieval
    # optimized_hits = model.sparse_retriever.search(optimized_query, k=10)
    # optimized_docs = [hit.docid for hit in optimized_hits]
    test_dict_2[qid]={}

    opt_scores = qoqa.sparse_retriever.get_scores(optimized_query)

    # top_n_new_docids = sorted(range(len(opt_scores)), key=lambda i: opt_scores[i], reverse=True)[:10]
    top_n = 10
    top_n_docids_with_indices = sorted(
        enumerate(opt_scores),  # Pair (index, score)
        key=lambda x: x[1],  # Sort by score
        reverse=True  # Descending order
    )[:top_n]
    top_n_docids = [doc_ids[idx] for idx, score in top_n_docids_with_indices]  # Extract indices
    top_n_scores = [score for idx, score in top_n_docids_with_indices]
    # top_n_docids = sorted(range(len(bm25_scores)), key=lambda i: bm25_scores[i], reverse=True)[:10]
    test_dict_2[qid]={}

    for i in range(0,top_n):
      passageid= top_n_docids[i]
      test_dict_2[qid][passageid]=top_n_scores[i]

    # Calculate optimized NDCG@10
    # optimized_ndcg = calculate_ndcg(top_n_new_docids, filtered_qrels[str(qid)], k=10)

    # ndcg_scores_optimized.append(optimized_ndcg)
    # ndcg_scores_sparse.append(original_ndcg)

  0%|          | 0/100 [00:00<?, ?it/s]

get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[3.39413228 3.49473191 0.         ... 0.         0.         0.        ]
optimize_query - start- QOQA
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[3.39413228 3.49473191 0.         ... 0.         0.         0.        ]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[134.7498594  133.97548027 146.91714478 ...  98.52957153 120.4545517
 107.00537109]
get__hybrid_scores - end- QOQA
generate_rephrased_query - start- QOQA
_create_prompt - start- QOQA
_create_prompt - end - QOQA
My goal is to make a rephrased query to retrieve answer documents with high scores.
Query: Why Deep Fried Foods May Cause Cancer

Top-5 retrieved docs:
1. Processed meat intake may be involved in the etiology of colorectal cancer, a major cause of death in affluent countries. The epidemiologic studies published to date conclude that the excess risk in t...
2. Events be

  1%|          | 1/100 [00:06<10:07,  6.13s/it]

get_scores - end- SparseRetriever
[198.84666278 175.20096525 154.35663447 ... 140.86166591 162.33956202
 153.35753307]
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[2.48953727 0.         2.00216223 ... 0.         3.32871617 3.18873699]
optimize_query - start- QOQA
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[2.48953727 0.         2.00216223 ... 0.         3.32871617 3.18873699]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[122.46311846 118.33772278 125.97132676 ...  93.47999573 101.36206931
 121.04372721]
get__hybrid_scores - end- QOQA
generate_rephrased_query - start- QOQA
_create_prompt - start- QOQA
_create_prompt - end - QOQA
My goal is to make a rephrased query to retrieve answer documents with high scores.
Query: Living Longer by Reducing Leucine Intake

Top-5 retrieved docs:
1. Summary Reduced function mutations in the insulin/IGF-I signaling pathway increase maximal li

  2%|▏         | 2/100 [00:11<09:11,  5.63s/it]

...

generate_rephrased_query - end- QOQA
Doctor who developed a groundbreaking diet therapy for patients with accelerated hypertension at Duke University
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[10.17948535  5.52333275  8.64397837 ...  5.54236634  4.24886773
  6.20985903]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[116.45427361 116.26993887 110.2600735  ...  94.81848834  89.98275573
 108.39839832]
get__hybrid_scores - end- QOQA
optimize_query - end- QOQA
Physician who implemented a radical diet regimen for treating malignant hypertension at Duke University
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[5.47562002 5.52333275 5.45016676 ... 5.54236634 4.24886773 6.20985903]
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[0. 0. 0. ... 0. 0. 0.]
optimize_query - start- QOQA
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - en

 99%|█████████▉| 99/100 [08:46<00:05,  5.01s/it]

get_scores - end- SparseRetriever
[149.72853479 142.91853929 122.11852083 ... 124.28531281 114.30178891
 132.31662731]
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[0. 0. 0. ... 0. 0. 0.]
optimize_query - start- QOQA
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[0. 0. 0. ... 0. 0. 0.]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[83.27297211 69.05023956 89.60868835 ... 63.63446045 84.56021118
 90.76744843]
get__hybrid_scores - end- QOQA
generate_rephrased_query - start- QOQA
_create_prompt - start- QOQA
_create_prompt - end - QOQA
My goal is to make a rephrased query to retrieve answer documents with high scores.
Query: Easter Island

Top-5 retrieved docs:
1. Background Prenatal exposure to mercury has been associated with adverse childhood neurologic outcomes in epidemiologic studies. Dose–response information for this relationship is useful for estimatin...
2. Background Pren

100%|██████████| 100/100 [08:51<00:00,  5.31s/it]

generate_rephrased_query - end- QOQA
Investigate the correlation between Easter Island and the prevalence of ichthyosarcotoxic outbreaks in Réunion
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[18.62765467 18.24653903 17.95188057 ... 20.08868895 18.77375089
 19.49697124]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[115.88162533 110.33618955 116.36085426 ...  86.49441882 111.90111776
 110.26257096]
get__hybrid_scores - end- QOQA
optimize_query - end- QOQA
Explore the interactions between Easter Island and goitrogenic vegetables in relation to thyroid cancer risk
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[18.41799407 19.15630822 13.9430622  ... 16.05683799 15.57138016
 14.91702842]


In [ ]:
top_n_docids

['MED-3445',
 'MED-2521',
 'MED-3444',
 'MED-3199',
 'MED-3703',
 'MED-3448',
 'MED-3620',
 'MED-2258',
 'MED-5111',
 'MED-4861']

In [ ]:
!pip install pytrec_eval


  Preparing metadata (setup.py) ... done
  Created wheel for pytrec_eval: filename=pytrec_eval-0.5-cp310-cp310-linux_x86_64.whl size=308215 sha256=409c642cb12a3a3df260b28c6d358c2ffa07011648241bace664a3629cd2752d
  Stored in directory: /root/.cache/pip/wheels/51/3a/cd/dcc1ddfc763987d5cb237165d8ac249aa98a23ab90f67317a8
Successfully built pytrec_eval


In [ ]:
import pytrec_eval

In [ ]:
evaluator = pytrec_eval.RelevanceEvaluator(qrels, {'P.3,5,10', 'ndcg_cut.3,5,10', 'recall.3,5,10','map_cut.3,5,10'})
result = evaluator.evaluate(test_dict)
print(result)
metrics = ['P','ndcg_cut', 'recall', 'map_cut']
cutoffs = [3,5,10]
scores = {f'{metric}_{cutoff}': 0 for metric in metrics for cutoff in cutoffs}
for key in result:
  for metric in metrics:
    for cutoff in cutoffs:
      scores[f'{metric}_{cutoff}'] += result[key][f'{metric}_{cutoff}']
run_length = len(test_dict)
for score in scores:
  scores[score] /= run_length

{'PLAIN-1': {'P_3': 0.3333333333333333, 'P_5': 0.2, 'P_10': 0.1, 'recall_3': 0.02040816326530612, 'recall_5': 0.02040816326530612, 'recall_10': 0.02040816326530612, 'ndcg_cut_3': 0.23463936301137822, 'ndcg_cut_5': 0.16958010263680806, 'ndcg_cut_10': 0.11768826558093261, 'map_cut_3': 0.006802721088435374, 'map_cut_5': 0.006802721088435374, 'map_cut_10': 0.006802721088435374}, 'PLAIN-11': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 0.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.0, 'ndcg_cut_10': 0.0, 'map_cut_3': 0.0, 'map_cut_5': 0.0, 'map_cut_10': 0.0}, 'PLAIN-22': {'P_3': 0.0, 'P_5': 0.2, 'P_10': 0.1, 'recall_3': 0.0, 'recall_5': 0.022727272727272728, 'recall_10': 0.022727272727272728, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.07020838719835952, 'ndcg_cut_10': 0.054446697840052224, 'map_cut_3': 0.0, 'map_cut_5': 0.004545454545454546, 'map_cut_10': 0.004545454545454546}, 'PLAIN-32': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'recall_3': 0.0, 'recall_5': 0.0, 'reca

In [ ]:
#bm25 i=3, q=100, general

In [ ]:
scores

{'P_3': 0.21000000000000005,
 'P_5': 0.17799999999999994,
 'P_10': 0.12199999999999996,
 'ndcg_cut_3': 0.22083658437698198,
 'ndcg_cut_5': 0.20525846777833134,
 'ndcg_cut_10': 0.17903680794875,
 'recall_3': 0.06390307440322746,
 'recall_5': 0.07762774645848641,
 'recall_10': 0.08796560126621784,
 'map_cut_3': 0.05456337651389638,
 'map_cut_5': 0.062325531913705136,
 'map_cut_10': 0.06761183861963067}

In [ ]:
evaluator = pytrec_eval.RelevanceEvaluator(qrels, {'P.3,5,10', 'ndcg_cut.3,5,10', 'recall.3,5,10','map_cut.3,5,10'})
result = evaluator.evaluate(test_dict_2)
print(result)
metrics = ['P','ndcg_cut', 'recall', 'map_cut']
cutoffs = [3,5,10]
scores = {f'{metric}_{cutoff}': 0 for metric in metrics for cutoff in cutoffs}
for key in result:
  for metric in metrics:
    for cutoff in cutoffs:
      scores[f'{metric}_{cutoff}'] += result[key][f'{metric}_{cutoff}']
run_length = len(test_dict)
for score in scores:
  scores[score] /= run_length

{'PLAIN-1': {'P_3': 0.6666666666666666, 'P_5': 0.6, 'P_10': 0.3, 'recall_3': 0.04081632653061224, 'recall_5': 0.061224489795918366, 'recall_10': 0.061224489795918366, 'ndcg_cut_3': 0.5307212739772434, 'ndcg_cut_5': 0.4566005422926888, 'ndcg_cut_10': 0.31687989952941614, 'map_cut_3': 0.04081632653061224, 'map_cut_5': 0.05612244897959184, 'map_cut_10': 0.05612244897959184}, 'PLAIN-11': {'P_3': 0.6666666666666666, 'P_5': 0.4, 'P_10': 0.6, 'recall_3': 0.03508771929824561, 'recall_5': 0.03508771929824561, 'recall_10': 0.10526315789473684, 'ndcg_cut_3': 0.46927872602275644, 'ndcg_cut_5': 0.3391602052736161, 'ndcg_cut_10': 0.4683402682779442, 'map_cut_3': 0.029239766081871343, 'map_cut_5': 0.029239766081871343, 'map_cut_10': 0.07069757727652465}, 'PLAIN-22': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 0.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.0, 'ndcg_cut_10': 0.0, 'map_cut_3': 0.0, 'map_cut_5': 0.0, 'map_cut_10': 0.0}, 'PLAIN-32': {'P_3': 0.0, 'P_5': 0.

In [ ]:
#bm25 i=3, q=100, optimized

In [ ]:
scores

{'P_3': 0.30666666666666664,
 'P_5': 0.2819999999999999,
 'P_10': 0.21099999999999994,
 'ndcg_cut_3': 0.29156059572339954,
 'ndcg_cut_5': 0.28810752265957335,
 'ndcg_cut_10': 0.26718640498439233,
 'recall_3': 0.0753385502664821,
 'recall_5': 0.11357733091568123,
 'recall_10': 0.14874832574328695,
 'map_cut_3': 0.06606754535257432,
 'map_cut_5': 0.0887352995072074,
 'map_cut_10': 0.10545626595522453}

In [ ]:
# DR run with 100 qrels and i=3

In [ ]:
ndcg_scores_optimized = []
ndcg_scores_sparse = []
test_dict={}
test_dict_2={}
query_ids = list(qrels.keys())[:100]
for qid in tqdm(query_ids):
    # Original query retrieval
    # original_hits = model.sparse_retriever.search(queries[qid], k=10)
    # original_docs = [hit.docid for hit in original_hits]
    # bm25_scores = qoqa.sparse_retriever.get_scores(queries[qid])
    query_embedding = qoqa.dense_retriever.encode([queries[qid]])[0]
    dense_scores = np.dot(qoqa.doc_embeddings, query_embedding)
    top_n = 10
    top_n_docids_with_indices = sorted(
        enumerate(dense_scores),  # Pair (index, score)
        key=lambda x: x[1],  # Sort by score
        reverse=True  # Descending order
    )[:top_n]
    print(top_n_docids_with_indices)
    top_n_docids = [doc_ids[idx] for idx, score in top_n_docids_with_indices]  # Extract indices
    top_n_scores = [score for idx, score in top_n_docids_with_indices]
    # top_n_docids = sorted(range(len(bm25_scores)), key=lambda i: bm25_scores[i], reverse=True)[:10]
    test_dict[qid]={}

    for i in range(0,top_n):
      passageid= top_n_docids[i]
      test_dict[qid][passageid]=top_n_scores[i]
    # sorted_passages = sorted(test_dict[qid].items(), key=lambda item: item[1], reverse=True)
    # test_dict[qid] = dict(sorted_passages[:10])


    # print(test_dict)

    # Calculate original NDCG@10
    # original_ndcg = calculate_ndcg(top_n_docids, filtered_qrels[str(qid)], k=10)

    # Optimize query
    optimized_query = qoqa.optimize_query(queries[qid])

    # Optimized query retrieval
    # optimized_hits = model.sparse_retriever.search(optimized_query, k=10)
    # optimized_docs = [hit.docid for hit in optimized_hits]
    test_dict_2[qid]={}
    # opt_scores = qoqa.sparse_retriever.get_scores(optimized_query)
    query_embedding = qoqa.dense_retriever.encode([optimized_query])[0]
    opt_dense_scores = np.dot(qoqa.doc_embeddings, query_embedding)
    # top_n_new_docids = sorted(range(len(opt_scores)), key=lambda i: opt_scores[i], reverse=True)[:10]
    top_n = 10
    top_n_docids_with_indices = sorted(
        enumerate(opt_dense_scores),  # Pair (index, score)
        key=lambda x: x[1],  # Sort by score
        reverse=True  # Descending order
    )[:top_n]
    top_n_docids = [doc_ids[idx] for idx, score in top_n_docids_with_indices]  # Extract indices
    top_n_scores = [score for idx, score in top_n_docids_with_indices]
    # top_n_docids = sorted(range(len(bm25_scores)), key=lambda i: bm25_scores[i], reverse=True)[:10]
    test_dict_2[qid]={}

    for i in range(0,top_n):
      passageid= top_n_docids[i]
      test_dict_2[qid][passageid]=top_n_scores[i]

    # Calculate optimized NDCG@10
    # optimized_ndcg = calculate_ndcg(top_n_new_docids, filtered_qrels[str(qid)], k=10)

    # ndcg_scores_optimized.append(optimized_ndcg)
    # ndcg_scores_sparse.append(original_ndcg)

  0%|          | 0/100 [00:00<?, ?it/s]

encode - start- Dense Retriever done
encode - end -Dense Retriever done
[(1364, 215.14417), (2483, 198.4116), (3513, 190.71701), (1369, 188.258), (2815, 181.7801), (3289, 179.75577), (312, 179.72137), (1183, 179.25653), (2285, 179.04614), (3434, 179.02087)]
optimize_query - start- QOQA
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[3.39413228 3.49473191 0.         ... 0.         0.         0.        ]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[134.7498594  133.97548027 146.91714478 ...  98.52957153 120.4545517
 107.00537109]
get__hybrid_scores - end- QOQA
generate_rephrased_query - start- QOQA
_create_prompt - start- QOQA
_create_prompt - end - QOQA
My goal is to make a rephrased query to retrieve answer documents with high scores.
Query: Why Deep Fried Foods May Cause Cancer

Top-5 retrieved docs:
1. Processed meat intake may be involved in the etiology of colorectal cancer, a major cause of death i

  1%|          | 1/100 [00:07<12:23,  7.51s/it]

generate_rephrased_query - end- QOQA
What are the potential health risks associated with the consistent consumption of deep-fried foods?
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[14.86373578 10.1238649  17.75100642 ... 13.91162033 16.82056892
 11.87379978]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[125.01186339 115.97146242 145.41749566 ... 111.71848595 128.87701081
 111.17877402]
get__hybrid_scores - end- QOQA
optimize_query - end- QOQA
What are the potential cancer risks associated with consuming deep-fried foods?] 

Top-5 retrieved docs:
1. BACKGROUND AND AIM: Currently, more than 30% of the caloric intake in the Colombian population comes from vegetable oil consumption mainly by the ingestion of deep-fried foods. Recently, it has been r...
2. Evidence suggests that high-heat cooking methods may increase the risk of prostate cancer (PCa). The addition of oil/fat, as in deep-frying, may be of 

  2%|▏         | 2/100 [00:14<11:29,  7.03s/it]

...

generate_rephrased_query - end- QOQA
What contributions did Dr. Walter Kempner make to the medical field?
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[ 6.83371941  6.71848801  6.64433398 ... 12.9625946   7.84183002
  7.2088134 ]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[ 94.43557684  95.67789128  98.63468639 ...  89.18709808 101.98318813
  94.65791595]
get__hybrid_scores - end- QOQA
optimize_query - end- QOQA
Who is Dr. Walter Kempner?]

Top-5 retrieved docs:
1. In 1940, a young German refugee physician scientist at Duke University in Durham, North Carolina began to treat patients with accelerated or "malignant" hypertension with a radical diet consisting of ...
2. In a 1995 pivotal study, Kushner described the attitudes, practice behaviors, and barriers to the delivery of nutrition counseling by primary care physicians. This article recognized nutrition and die...
3. OBJECTIVES: To determine the 

 99%|█████████▉| 99/100 [09:12<00:04,  4.45s/it]

generate_rephrased_query - end- QOQA
Investigate the presence and potential benefits of dulse in Indian traditional Ayurvedic medicines, focusing on its health effects.
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[17.65737349 14.39092442 14.5013582  ... 17.4725367  21.62034289
 17.06807012]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[116.26999455 111.42672519 111.98220979 ... 112.08821131 126.29752471
 112.04231727]
get__hybrid_scores - end- QOQA
optimize_query - end- QOQA
Examine the impact of dulse in Indian-manufactured traditional Ayurvedic medicines and its implications for health.
encode - start- Dense Retriever done
encode - end -Dense Retriever done
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[(1978, 136.74416), (2676, 133.6582), (667, 130.76843), (1671, 129.24323), (1736, 129.24321), (2948, 127.713974), (1981, 127.65827), (3604, 126.87138), (1977, 126.68297), (17

100%|██████████| 100/100 [09:19<00:00,  5.59s/it]

generate_rephrased_query - end- QOQA
Explore the impact of prenatal exposure to mercury on childhood neurological outcomes in epidemiological studies
get__hybrid_scores - start- QOQA
get_scores - start- SparseRetriever
get_scores - end- SparseRetriever
[18.05674338 14.98331542 13.84696395 ... 14.89448918 22.22740702
 15.85555554]
encode - start- Dense Retriever done
encode - end -Dense Retriever done
[125.75995901 122.30772638 138.04552403 ... 103.2158512  131.54344993
 107.86152601]
get__hybrid_scores - end- QOQA
optimize_query - end- QOQA
Research on the impact of prenatal exposure to mercury on childhood neurologic outcomes in epidemiologic studies]

Top-5 retrieved docs:
1. Background Prenatal exposure to mercury has been associated with adverse childhood neurologic outcomes in epidemiologic studies. Dose–response information for this relationship is useful for estimatin...
2. Background Prenatal exposure to mercury has been associated with adverse childhood neurologic outcomes in 

In [ ]:
test_dict_converted = {
    query_id: {doc_id: float(score) for doc_id, score in doc_scores.items()}
    for query_id, doc_scores in test_dict.items()
}

In [ ]:
test_dict_converted_2 = {
    query_id: {doc_id: float(score) for doc_id, score in doc_scores.items()}
    for query_id, doc_scores in test_dict_2.items()
}

In [ ]:

evaluator = pytrec_eval.RelevanceEvaluator(qrels, {'P.3,5,10', 'ndcg_cut.3,5,10', 'recall.3,5,10','map_cut.3,5,10'})
result = evaluator.evaluate(test_dict_converted)
print(result)
metrics = ['P','ndcg_cut', 'recall', 'map_cut']
cutoffs = [3,5,10]
scores = {f'{metric}_{cutoff}': 0 for metric in metrics for cutoff in cutoffs}
for key in result:
  for metric in metrics:
    for cutoff in cutoffs:
      scores[f'{metric}_{cutoff}'] += result[key][f'{metric}_{cutoff}']
run_length = len(test_dict)
for score in scores:
  scores[score] /= run_length

{'PLAIN-1': {'P_3': 0.6666666666666666, 'P_5': 0.6, 'P_10': 0.3, 'recall_3': 0.04081632653061224, 'recall_5': 0.061224489795918366, 'recall_10': 0.061224489795918366, 'ndcg_cut_3': 0.617319681505689, 'ndcg_cut_5': 0.5191875125622332, 'ndcg_cut_10': 0.3603151367091187, 'map_cut_3': 0.04081632653061224, 'map_cut_5': 0.05612244897959184, 'map_cut_10': 0.05612244897959184}, 'PLAIN-11': {'P_3': 1.0, 'P_5': 0.6, 'P_10': 0.6, 'recall_3': 0.05263157894736842, 'recall_5': 0.05263157894736842, 'recall_10': 0.10526315789473684, 'ndcg_cut_3': 0.7653606369886217, 'ndcg_cut_5': 0.5531464700081437, 'ndcg_cut_10': 0.5338387900521387, 'map_cut_3': 0.05263157894736842, 'map_cut_5': 0.05263157894736842, 'map_cut_10': 0.08698830409356724}, 'PLAIN-22': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 0.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.0, 'ndcg_cut_10': 0.0, 'map_cut_3': 0.0, 'map_cut_5': 0.0, 'map_cut_10': 0.0}, 'PLAIN-32': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'rec

In [ ]:
# DR, I =3, Q=100, general

In [ ]:
scores

{'P_3': 0.3466666666666668,
 'P_5': 0.3079999999999999,
 'P_10': 0.24499999999999994,
 'ndcg_cut_3': 0.3398553359954193,
 'ndcg_cut_5': 0.3248277909152247,
 'ndcg_cut_10': 0.3085897258521056,
 'recall_3': 0.08310113480835625,
 'recall_5': 0.11625753268722815,
 'recall_10': 0.15497145194325185,
 'map_cut_3': 0.0762714443952308,
 'map_cut_5': 0.09467411414851959,
 'map_cut_10': 0.11416725968966908}

In [ ]:
evaluator = pytrec_eval.RelevanceEvaluator(qrels, {'P.3,5,10', 'ndcg_cut.3,5,10', 'recall.3,5,10','map_cut.3,5,10'})
result = evaluator.evaluate(test_dict_converted_2)
print(result)
metrics = ['P','ndcg_cut', 'recall', 'map_cut']
cutoffs = [3,5,10]
scores = {f'{metric}_{cutoff}': 0 for metric in metrics for cutoff in cutoffs}
for key in result:
  for metric in metrics:
    for cutoff in cutoffs:
      scores[f'{metric}_{cutoff}'] += result[key][f'{metric}_{cutoff}']
run_length = len(test_dict)
for score in scores:
  scores[score] /= run_length

{'PLAIN-1': {'P_3': 1.0, 'P_5': 0.6, 'P_10': 0.3, 'recall_3': 0.061224489795918366, 'recall_5': 0.061224489795918366, 'recall_10': 0.061224489795918366, 'ndcg_cut_3': 0.7346393630113782, 'ndcg_cut_5': 0.530943388959284, 'ndcg_cut_10': 0.3684736923535616, 'map_cut_3': 0.061224489795918366, 'map_cut_5': 0.061224489795918366, 'map_cut_10': 0.061224489795918366}, 'PLAIN-11': {'P_3': 0.6666666666666666, 'P_5': 0.8, 'P_10': 0.6, 'recall_3': 0.03508771929824561, 'recall_5': 0.07017543859649122, 'recall_10': 0.10526315789473684, 'ndcg_cut_3': 0.5307212739772434, 'ndcg_cut_5': 0.6608397947263839, 'ndcg_cut_10': 0.5342931669774931, 'map_cut_3': 0.03508771929824561, 'map_cut_5': 0.062280701754385964, 'map_cut_10': 0.08859649122807017}, 'PLAIN-22': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 0.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.0, 'ndcg_cut_10': 0.0, 'map_cut_3': 0.0, 'map_cut_5': 0.0, 'map_cut_10': 0.0}, 'PLAIN-32': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0,

In [ ]:
# DR, I =3, Q=100, opt

In [ ]:
scores

{'P_3': 0.33666666666666667,
 'P_5': 0.3019999999999999,
 'P_10': 0.23299999999999993,
 'ndcg_cut_3': 0.3085468660978317,
 'ndcg_cut_5': 0.30530600543994324,
 'ndcg_cut_10': 0.2856864346504582,
 'recall_3': 0.07754851596643447,
 'recall_5': 0.12169850997073695,
 'recall_10': 0.15492641715972963,
 'map_cut_3': 0.06733108463357469,
 'map_cut_5': 0.08978551218370438,
 'map_cut_10': 0.11035199332418562}